Git clone the repo and install the requirements. (ignore the pip errors about protobuf)

In [ ]:
#@title # 1. Установка sistine/chapel и подготовка среды окружения

import os
from pathlib import Path

!apt-get install libgoogle-perftools-dev sox ffmpeg libcairo2 libcairo2-dev
!ln -s libtcmalloc.so.4 libtcmalloc.so
os.environ.setdefault('LD_PRELOAD', '/usr/lib/x86_64-linux-gnu/libtcmalloc.so')
os.environ.setdefault('TF_CPP_MIN_LOG_LEVEL', '2')
os.environ.setdefault('ACCELERATE', 'True')
os.environ.setdefault('FORCE_CUDA', '1')
os.environ.setdefault('ATTN_PRECISION', 'fp16')
os.environ.setdefault('PYTORCH_CUDA_ALLOC_CONF', 'garbage_collection_threshold:0.8,max_split_size_mb:512')   # ещё вариант max_split_size_mb:128
os.environ.setdefault('CUDA_LAUNCH_BLOCKING', '0')
os.environ.setdefault('CUDA_CACHE_DISABLE', '0')
os.environ.setdefault('CUDA_AUTO_BOOST', '1')
os.environ.setdefault('CUDA_MODULE_LOADING', 'LAZY')
os.environ.setdefault('CUDA_DEVICE_DEFAULT_PERSISTING_L2_CACHE_PERCENTAGE_LIMIT', '0')
os.environ.setdefault('GRADIO_ANALYTICS_ENABLED', 'False')
os.environ.setdefault('SAFETENSORS_FAST_GPU', '1')
os.environ.setdefault('NUMEXPR_MAX_THREADS', '16')
os.environ.setdefault('PYTHONHTTPSVERIFY', '0')
os.environ.setdefault('HF_HUB_DISABLE_TELEMETRY', '1')
os.environ.setdefault('UVICORN_TIMEOUT_KEEP_ALIVE', '60')

OPTIONS = {}

# USE_GOOGLE_DRIVE = False  #@param {type:"boolean"}

WORKSPACE = '/content'
# OPTIONS['USE_GOOGLE_DRIVE'] = USE_GOOGLE_DRIVE

# if OPTIONS['USE_GOOGLE_DRIVE']:
#     !echo "Mounting Google Drive..."
#     %cd /

#     from google.colab import drive
#     drive.mount('/content/drive')

#     WORKSPACE = "/content/drive/MyDrive"
#     %cd /content/drive/MyDrive

%cd /content
![ ! -d $WORKSPACE ] && echo -= Initial setup sistine/chapel =- 
!wget -q -O /content/sistinechapelo https://raw.githubusercontent.com/operatortob/facerestore/sistinechapel/sistinechapelo.py
!python sistinechapelo && rm -r /content/sistinechapelo
%cd $WORKSPACE/sistine/chapel


!echo -= Install dependencies =-
!pip install xformers!=0.0.18 -r requirements.txt --extra-index-url https://download.pytorch.org/whl/cu118 --extra-index-url https://download.pytorch.org/whl/cu117

%cd /content/sistine/chapel/custom_nodes
!git clone https://github.com/ltdrdata/ComfyUI-Manager.git

!git clone https://github.com/Gourieff/comfyui-reactor-node.git
%cd /content/sistine/chapel/custom_nodes/comfyui-reactor-node/
!python install.py

%cd /content/sistine/chapel/custom_nodes
!git clone -b facerestore https://github.com/operatortob/facerestore.git
%cd /content/sistine/chapel/custom_nodes/facerestore
!pip install -r requirements.txt

#убираем ошибку reactor ['AzureExecutionProvider...
#!python -m pip install -U pip
!pip uninstall -y onnx onnxruntime onnxruntime-gpu onnxruntime-silicon onnxruntime-extensions
!pip install onnx==1.14.1 onnxruntime==1.15.1

!mkdir -p /content/sistine/chapel/models/facerestore_models/
!mkdir -p /content/sistine/chapel/models/facedetection/
!wget -O /content/sistine/chapel/models/facerestore_models/codeformer.pth 'https://github.com/sczhou/CodeFormer/releases/download/v0.1.0/codeformer.pth'
!wget -O /content/sistine/chapel/models/facerestore_models/GFPGANv1.3.pth 'https://github.com/TencentARC/GFPGAN/releases/download/v1.3.0/GFPGANv1.3.pth'
!wget -O /content/sistine/chapel/models/facerestore_models/GFPGANv1.4.pth 'https://github.com/TencentARC/GFPGAN/releases/download/v1.3.4/GFPGANv1.4.pth'
!wget -O /content/sistine/chapel/models/facedetection/detection_Resnet50_Final.pth 'https://github.com/xinntao/facexlib/releases/download/v0.1.0/detection_Resnet50_Final.pth'
!wget -O /content/sistine/chapel/models/facedetection/detection_mobilenet0.25_Final.pth 'https://github.com/xinntao/facexlib/releases/download/v0.1.0/detection_mobilenet0.25_Final.pth'
!wget -O /content/sistine/chapel/models/facedetection/yolov5l-face.pth 'https://github.com/sczhou/CodeFormer/releases/download/v0.1.0/yolov5l-face.pth'
!wget -O /content/sistine/chapel/models/facedetection/yolov5n-face.pth 'https://github.com/sczhou/CodeFormer/releases/download/v0.1.0/yolov5n-face.pth'
!wget -O /content/sistine/chapel/models/facedetection/parsing_parsenet.pth 'https://github.com/sczhou/CodeFormer/releases/download/v0.1.0/parsing_parsenet.pth'
if not os.path.exists('/content/sistine/chapel/custom_nodes/comfyui-reactor-node/models/facerestore_models'):
    !mkdir -p /content/sistine/chapel/custom_nodes/comfyui-reactor-node/models/facerestore_models
!cp -rfdl /content/sistine/chapel/models/facerestore_models/* -t /content/sistine/chapel/custom_nodes/comfyui-reactor-node/models/facerestore_models

%cd $WORKSPACE/sistine/chapel


Download some models/checkpoints/vae or custom sistine/chapel nodes (uncomment the commands for the ones you want)

In [ ]:
#@title # 2. Загрузка моделей
# Checkpoints
%cd $WORKSPACE/sistine/chapel

SDXL_model_name = "None" # @param ["None", "xxmix9realisticsdxl_testV20", "sdvn6Realxl_beautyface", "physiogenXL_v04", "realmixXL_v10", "cherryPickerXL_v20", "xlYamersRealistic_v3", "nightvisionXLPhotorealisticPortrait_beta0681Bakedvae", "zavychromaxl_b2" ]

# URL-ы для разных моделей
model_urls = {
    "sdvn6Realxl_beautyface": "https://civitai.com/api/download/models/130249?type=Model&format=SafeTensor&size=full&fp=fp16",
    "physiogenXL_v04": "https://civitai.com/api/download/models/139477?type=Model&format=SafeTensor&size=full&fp=fp16",
    "realmixXL_v10": "https://civitai.com/api/download/models/135858?type=Model&format=SafeTensor&size=full&fp=fp16",
    "cherryPickerXL_v20": "https://civitai.com/api/download/models/143431?type=Model&format=SafeTensor&size=pruned&fp=fp16",
    "xlYamersRealistic_v3": "https://civitai.com/api/download/models/144590?type=Model&format=SafeTensor&size=full&fp=fp16",
    "nightvisionXLPhotorealisticPortrait_beta0681Bakedvae": "https://civitai.com/api/download/models/146882?type=Model&format=SafeTensor&size=pruned&fp=fp16",
    "zavychromaxl_b2": "https://civitai.com/api/download/models/140608?type=Model&format=SafeTensor&size=full&fp=fp16",
    "xxmix9realisticsdxl_testV20": "https://civitai.com/api/download/models/145282?type=Model&format=SafeTensor&size=full&fp=bf16",
}

# Загружаем модель с соответствующим URL
if SDXL_model_name in model_urls:
    model_url = model_urls[SDXL_model_name]
    !wget --content-disposition --trust-server-names -P /content/sistine/chapel/models/checkpoints/ $model_url

# @markdown Укажите URL прямую ссылку на модель SDXL
SDXL_model_URL_for_downloading = "" # @param {type:"string"}

if not SDXL_model_URL_for_downloading == "":
    !wget --content-disposition --trust-server-names -P /content/sistine/chapel/models/checkpoints/ $SDXL_model_URL_for_downloading

### SDXL
### I recommend these workflow examples: https://comfyanonymous.github.io/ComfyUI_examples/sdxl/

# @markdown Загрузить оригинальную базовую модель SDXL 1.0 от Stabilityai
download_SDXL_base = True # @param {type:"boolean"}
download_SDXL_refiner = True # @param {type:"boolean"}

if download_SDXL_base:
    !wget -c https://huggingface.co/stabilityai/stable-diffusion-xl-base-1.0/resolve/main/sd_xl_base_1.0_0.9vae.safetensors -P /content/sistine/chapel/models/checkpoints/

if download_SDXL_refiner:
    !wget -c https://huggingface.co/stabilityai/stable-diffusion-xl-refiner-1.0/resolve/main/sd_xl_refiner_1.0_0.9vae.safetensors -P /content/sistine/chapel/models/checkpoints/


# SD1.5
#!wget -c https://huggingface.co/runwayml/stable-diffusion-v1-5/resolve/main/v1-5-pruned-emaonly.ckpt -P ./models/checkpoints/

# SD2
#!wget -c https://huggingface.co/stabilityai/stable-diffusion-2-1-base/resolve/main/v2-1_512-ema-pruned.safetensors -P ./models/checkpoints/
#!wget -c https://huggingface.co/stabilityai/stable-diffusion-2-1/resolve/main/v2-1_768-ema-pruned.safetensors -P ./models/checkpoints/

# Some SD1.5 anime style
#!wget -c https://huggingface.co/WarriorMama777/OrangeMixs/resolve/main/Models/AbyssOrangeMix2/AbyssOrangeMix2_hard.safetensors -P ./models/checkpoints/
#!wget -c https://huggingface.co/WarriorMama777/OrangeMixs/resolve/main/Models/AbyssOrangeMix3/AOM3A1_orangemixs.safetensors -P ./models/checkpoints/
#!wget -c https://huggingface.co/WarriorMama777/OrangeMixs/resolve/main/Models/AbyssOrangeMix3/AOM3A3_orangemixs.safetensors -P ./models/checkpoints/
#!wget -c https://huggingface.co/Linaqruf/anything-v3.0/resolve/main/anything-v3-fp16-pruned.safetensors -P ./models/checkpoints/

# Waifu Diffusion 1.5 (anime style SD2.x 768-v)
#!wget -c https://huggingface.co/waifu-diffusion/wd-1-5-beta3/resolve/main/wd-illusion-fp16.safetensors -P ./models/checkpoints/


# unCLIP models
#!wget -c https://huggingface.co/comfyanonymous/illuminatiDiffusionV1_v11_unCLIP/resolve/main/illuminatiDiffusionV1_v11-unclip-h-fp16.safetensors -P ./models/checkpoints/
#!wget -c https://huggingface.co/comfyanonymous/wd-1.5-beta2_unCLIP/resolve/main/wd-1-5-beta2-aesthetic-unclip-h-fp16.safetensors -P ./models/checkpoints/


# VAE
#!wget -c https://huggingface.co/stabilityai/sd-vae-ft-mse-original/resolve/main/vae-ft-mse-840000-ema-pruned.safetensors -P ./models/vae
!wget -c https://huggingface.co/stabilityai/sdxl-vae/resolve/main/sdxl_vae.safetensors -P $WORKSPACE/sistine/chapel/models/vae
#!wget -c https://huggingface.co/WarriorMama777/OrangeMixs/resolve/main/VAEs/orangemix.vae.pt -P ./models/vae/
#!wget -c https://huggingface.co/hakurei/waifu-diffusion-v1-4/resolve/main/vae/kl-f8-anime2.ckpt -P ./models/vae/


# Loras
#!wget -c https://civitai.com/api/download/models/10350 -O ./models/loras/theovercomer8sContrastFix_sd21768.safetensors #theovercomer8sContrastFix SD2.x 768-v
#!wget -c https://civitai.com/api/download/models/10638 -O ./models/loras/theovercomer8sContrastFix_sd15.safetensors #theovercomer8sContrastFix SD1.x
#!wget -c https://huggingface.co/stabilityai/stable-diffusion-xl-base-1.0/resolve/main/sd_xl_offset_example-lora_1.0.safetensors -P ./models/loras/ #SDXL offset noise lora


# T2I-Adapter
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_depth_sd14v1.pth -P ./models/controlnet/
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_seg_sd14v1.pth -P ./models/controlnet/
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_sketch_sd14v1.pth -P ./models/controlnet/
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_keypose_sd14v1.pth -P ./models/controlnet/
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_openpose_sd14v1.pth -P ./models/controlnet/
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_color_sd14v1.pth -P ./models/controlnet/
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_canny_sd14v1.pth -P ./models/controlnet/

# T2I Styles Model
#!wget -c https://huggingface.co/TencentARC/T2I-Adapter/resolve/main/models/t2iadapter_style_sd14v1.pth -P ./models/style_models/

# CLIPVision model (needed for styles model)
#!wget -c https://huggingface.co/openai/clip-vit-large-patch14/resolve/main/pytorch_model.bin -O ./models/clip_vision/clip_vit14.bin


# ControlNet
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11e_sd15_ip2p_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11e_sd15_shuffle_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_canny_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11f1p_sd15_depth_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_inpaint_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_lineart_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_mlsd_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_normalbae_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_openpose_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_scribble_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_seg_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15_softedge_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11p_sd15s2_lineart_anime_fp16.safetensors -P ./models/controlnet/
#!wget -c https://huggingface.co/comfyanonymous/ControlNet-v1-1_fp16_safetensors/resolve/main/control_v11u_sd15_tile_fp16.safetensors -P ./models/controlnet/


# Controlnet Preprocessor nodes by Fannovel16
#!cd custom_nodes && git clone https://github.com/Fannovel16/comfy_controlnet_preprocessors; cd comfy_controlnet_preprocessors && python install.py


# GLIGEN
#!wget -c https://huggingface.co/comfyanonymous/GLIGEN_pruned_safetensors/resolve/main/gligen_sd14_textbox_pruned_fp16.safetensors -P ./models/gligen/


# ESRGAN upscale model
!wget -c https://github.com/xinntao/Real-ESRGAN/releases/download/v0.1.0/RealESRGAN_x4plus.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/
!wget -c https://huggingface.co/sberbank-ai/Real-ESRGAN/resolve/main/RealESRGAN_x2.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/
!wget -c https://huggingface.co/sberbank-ai/Real-ESRGAN/resolve/main/RealESRGAN_x4.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/

!wget -c https://huggingface.co/uwg/upscaler/resolve/main/ESRGAN/8x_NMKD-Superscale_150000_G.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/
!wget -c https://huggingface.co/uwg/upscaler/resolve/main/ESRGAN/4x_NMKD-Siax_200k.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/
!wget -c https://huggingface.co/uwg/upscaler/resolve/main/ESRGAN/4x_NMKD-Superscale-SP_178000_G.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/
!wget -c https://huggingface.co/uwg/upscaler/resolve/main/ESRGAN/4x_foolhardy_Remacri.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/
!wget -c https://huggingface.co/uwg/upscaler/resolve/main/ESRGAN/4x-UltraSharp.pth -P $WORKSPACE/sistine/chapel/models/upscale_models/


In [ ]:
#@title # 3. Запуск ComfyUI
# @markdown *Run ComfyUI with localtunnel (Recommended Way)*
#@markdown  #### <br> Дополнительные аргументы запуска:

launch_cmd_args = "--dont-print-server --highvram" # @param {type:"string"}

!npm install -g localtunnel
%cd $WORKSPACE/sistine/chapel
import subprocess
import threading
import time
import socket
import urllib.request

def iframe_thread(port):
  while True:
      time.sleep(0.5)
      sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
      result = sock.connect_ex(('127.0.0.1', port))
      if result == 0:
        break
      sock.close()
  print("\n sistine/chapel finished loading, trying to launch localtunnel (if it gets stuck here localtunnel is having issues)\n")

  print("The password/enpoint ip for localtunnel is:", urllib.request.urlopen('https://ipv4.icanhazip.com').read().decode('utf8').strip("\n"))
  p = subprocess.Popen(["lt", "--port", "{}".format(port)], stdout=subprocess.PIPE)
  for line in p.stdout:
    print(line.decode(), end='')


threading.Thread(target=iframe_thread, daemon=True, args=(8188,)).start()
%cd $WORKSPACE/sistine/chapel
!python main.py $launch_cmd_args

### Run ComfyUI with colab iframe (use only in case the previous way with localtunnel doesn't work)

You should see the ui appear in an iframe. If you get a 403 error, it's your firefox settings or an extension that's messing things up.

If you want to open it in another window use the link.

Note that some UI features like live image previews won't work because the colab iframe blocks websockets.

In [ ]:
import threading
import time
import socket
def iframe_thread(port):
  while True:
      time.sleep(0.5)
      sock = socket.socket(socket.AF_INET, socket.SOCK_STREAM)
      result = sock.connect_ex(('127.0.0.1', port))
      if result == 0:
        break
      sock.close()
  from google.colab import output
  output.serve_kernel_port_as_iframe(port, height=1024)
  print("to open it in a window you can open this link here:")
  output.serve_kernel_port_as_window(port)

threading.Thread(target=iframe_thread, daemon=True, args=(8188,)).start()
%cd $WORKSPACE/sistine/chapel
!python main.py --dont-print-server